In [1]:
#General
import pandas as pd
import numpy as np
from sklearn.decomposition import PCA
import combat
from combat import combat
import patsy

#Normalization
from sklearn.preprocessing import StandardScaler

#Outlier removal
import scipy
from scipy import stats
from scipy.stats import zscore

#Heatmap
import seaborn as sns
import matplotlib.pyplot as plt
from matplotlib.pyplot import figure

In [ ]:
#pd.set_option('display.max_rows', 800)
#pd.set_option('display.max_columns', 800)

In [ ]:
#Creating a data frame for each group of lipids

data = pd.ExcelFile('200511_raw_dataset_all_modes_allkinases.xlsx')
df_cl = pd.read_excel(data, 'merged_cl')
df_p1 = pd.read_excel(data, 'merged_p1')
df_p2 = pd.read_excel(data, 'merged_p2')
df_n1 = pd.read_excel(data, 'merged_n1_OK')

In [ ]:
#copy dataframe 


data_cl = df_cl
data_p1 = df_p1
data_p2 = df_p2
data_n1 = df_n1

#Plot to see amount of measures in each series for each gene 
#data_cl.groupby(['Series_cl','GENE'])['GENE'].count().plot.bar()



In [ ]:
# convert the lipid columns to float

data_cl.iloc[:,9:123] = data_cl.iloc[:,9:123].apply(pd.to_numeric, errors='coerce')
data_p1.iloc[:,9:279] = data_p1.iloc[:,9:279].apply(pd.to_numeric, errors='coerce')
data_p2.iloc[:,9:206] = data_p2.iloc[:,9:206].apply(pd.to_numeric, errors='coerce')
data_n1.iloc[:,9:278] = data_n1.iloc[:,9:278].apply(pd.to_numeric, errors='coerce')


In [ ]:
# take the columns with less than 50 percent nan of total entries

data_cl = data_cl.loc[:, data_cl.isnull().sum() < 0.5*data_cl.shape[0]]
data_p1 = data_p1.loc[:, data_p1.isnull().sum() < 0.5*data_p1.shape[0]]
data_p2 = data_p2.loc[:, data_p2.isnull().sum() < 0.5*data_p2.shape[0]]
data_n1 = data_n1.loc[:, data_n1.isnull().sum() < 0.5*data_n1.shape[0]]


In [ ]:
# Eliminate standards

#convert to series
nunique_p2 = data_p2.apply(pd.Series.nunique)
nunique_p1 = data_p1.apply(pd.Series.nunique)
nunique_n1 = data_n1.apply(pd.Series.nunique)
nunique_cl = data_cl.apply(pd.Series.nunique)


# columns to drop
cols_to_drop_cl = nunique_cl[nunique_cl == 1].index
cols_to_drop_p1 = nunique_p1[nunique_p1 == 1].index
cols_to_drop_p2 = nunique_p2[nunique_p2 == 1].index
cols_to_drop_n1 = nunique_n1[nunique_n1 == 1].index

data_cl=data_cl.drop(cols_to_drop_cl, axis=1)
data_p1=data_p1.drop(cols_to_drop_p1, axis=1)
data_p2=data_p2.drop(cols_to_drop_p2, axis=1)
data_n1=data_n1.drop(cols_to_drop_n1, axis=1)

In [ ]:
#Goupby and replace NaN with mean for each GENE in each batch

data_cl = data_cl.groupby(['GENE','Series_cl']).apply(lambda x: x.fillna(x.mean()))
data_p1 = data_p1.groupby(['GENE','Series_p1']).apply(lambda x: x.fillna(x.mean()))
data_p2 = data_p2.groupby(['GENE','Series_p2']).apply(lambda x: x.fillna(x.mean()))
data_n1 = data_n1.groupby(['GENE','Series_p1']).apply(lambda x: x.fillna(x.mean()))

In [ ]:
#Reseting the index

data_cl = data_cl.reset_index(drop = True)
data_p1 = data_p1.reset_index(drop = True)
data_p2 = data_p2.reset_index(drop = True)
data_n1 = data_n1.reset_index(drop = True)

In [ ]:
#Replace NaN with mean for each GENE

data_cl = data_cl.groupby(['GENE']).apply(lambda x: x.fillna(x.mean()))
data_p1 = data_p1.groupby(['GENE']).apply(lambda x: x.fillna(x.mean()))
data_p2 = data_p2.groupby(['GENE']).apply(lambda x: x.fillna(x.mean()))
data_n1 = data_n1.groupby(['GENE']).apply(lambda x: x.fillna(x.mean()))

In [ ]:
#Reseting the index

data_cl = data_cl.reset_index(drop = True)
data_p1 = data_p1.reset_index(drop = True)
data_p2 = data_p2.reset_index(drop = True)
data_n1 = data_n1.reset_index(drop = True)

In [ ]:
#Replace NaN with mean of the column

data_cl.iloc[:,9:300] = data_cl.iloc[:,9:300].apply(lambda x: x.fillna(x.mean()))
data_n1.iloc[:,9:300] = data_n1.iloc[:,9:300].apply(lambda x: x.fillna(x.mean()))
data_p2.iloc[:,9:300] = data_p2.iloc[:,9:300].apply(lambda x: x.fillna(x.mean()))
data_p1.iloc[:,9:300] = data_p1.iloc[:,9:300].apply(lambda x: x.fillna(x.mean()))

In [ ]:
data_cl.to_csv('data_befbatch_cl.csv')
data_n1.to_csv('data_befbatch_n1.csv')
data_p2.to_csv('data_befbatch_p2.csv')
data_p1.to_csv('data_befbatch_p1.csv')

In [ ]:
data_cl = pd.read_csv('data_befbatch_cl.csv')
data_n1 = pd.read_csv('data_befbatch_n1.csv')
data_p2 = pd.read_csv('data_befbatch_p2.csv')
data_p1 = pd.read_csv('data_befbatch_p1.csv')

In [ ]:
#Elimination of unnecesary columns

data_cl=data_cl.drop(['Unnamed: 0','CP0_ID.BR','CP0_ID','BR','Good_bad','CP_plate','Toxic','CP0_ID.mode.BR'], axis=1)
data_n1=data_n1.drop(['Unnamed: 0','CP0_ID.BR','CP0_ID','BR','Good_bad','CP_plate','Toxic','CP0_ID.mode.BR'], axis=1)
data_p2=data_p2.drop(['Unnamed: 0','CP0_ID.BR','CP0_ID','BR','Good_bad','CP_plate','Toxic','CP0_ID.mode.BR'], axis=1)
data_p1=data_p1.drop(['Unnamed: 0','CP0_ID.BR','CP0_ID','BR','Good_bad','CP_plate','Toxic','CP0_ID.mode.BR'], axis=1)

In [ ]:
#Changin the name of the Series columns for "Batch"

data_cl.rename(columns = {'Series_cl':'Batch'}, inplace = True)
data_n1.rename(columns = {'Series_p1':'Batch'}, inplace = True)
data_p2.rename(columns = {'Series_p2':'Batch'}, inplace = True)
data_p1.rename(columns = {'Series_p1':'Batch'}, inplace = True)

In [ ]:
#Merging of the datasets of all the lipids

data_concat = pd.concat([data_cl, data_n1,data_p1,data_p2], axis=1)
data_concat = data_concat.loc[:,~data_concat.columns.duplicated()]

In [2]:
# Loading / Saving dataset

#data_concat.to_csv('data_concat.csv')
data_concat = pd.read_csv('data_concat.csv')
data_concat = data_concat.drop(['Unnamed: 0'], axis=1)

In [9]:
pd.set_option('display.max_rows', 10000)
data_concat['CL68:3_C16:0'].sort_values()

3271    2.348207e-07
5583    1.374781e-06
797     2.984861e-06
3604    5.247991e-06
719     6.040454e-06
4752    8.020032e-06
8250    1.037938e-05
8253    1.043691e-05
8675    1.256429e-05
8252    1.368787e-05
8254    1.592720e-05
8251    1.612885e-05
1890    1.818380e-05
8255    1.846807e-05
5674    2.071810e-05
9114    2.130513e-05
9118    2.133653e-05
5585    2.160503e-05
3475    2.177512e-05
3477    2.181962e-05
9117    2.210850e-05
9119    2.236534e-05
1892    2.326326e-05
3478    2.329928e-05
8120    2.480861e-05
3479    2.506014e-05
3630    2.507348e-05
5267    2.509343e-05
7905    2.526854e-05
9116    2.532448e-05
1895    2.533960e-05
4991    2.570194e-05
7902    2.649394e-05
1893    2.658046e-05
1891    2.687288e-05
9115    2.749700e-05
5263    2.789103e-05
5262    2.796682e-05
3476    2.831374e-05
3474    2.871941e-05
5266    2.935985e-05
5264    2.940457e-05
7904    2.972300e-05
7906    3.086204e-05
3631    3.088543e-05
5265    3.089010e-05
7903    3.154949e-05
1894    3.183

In [4]:
# Normalising the data by PC34:1
data_concat.iloc[:,2:755] = data_concat.iloc[:,2:755].div(data_concat['PC34:1'], axis=0)
data_concat = data_concat.drop(['PC34:1'], axis=1)

In [5]:
#Outliers removal INSIDE BATCH (z-score > 3)
z_scores = data_concat.groupby(['GENE','Batch']).transform(lambda x : zscore(x,ddof=1))
abs_z_scores = np.abs(z_scores)
filtered_entries = (abs_z_scores < 3).all(axis=1)
data_concat.iloc[:,2:755] = data_concat.iloc[:,2:755][filtered_entries]

/Users/pablo/opt/anaconda3/envs/lipidomics/lib/python3.8/site-packages/scipy/stats/stats.py:2419: RuntimeWarning: invalid value encountered in true_divide
  return (a - mns) / sstd


In [8]:
#Fill the NaNs generated by the removal of the outliers with the mean

data_concat = data_concat.groupby(['GENE','Batch']).apply(lambda x: x.fillna(x.mean()))
data_concat = data_concat.reset_index(drop = True)
data_concat = data_concat.groupby(['GENE']).apply(lambda x: x.fillna(x.mean()))
data_concat = data_concat.reset_index(drop = True)
data_concat.iloc[:,2:755] = data_concat.iloc[:,2:755].apply(lambda x: x.fillna(x.mean()))
data_concat = data_concat.reset_index(drop = True)

In [7]:
#Outliers removal OVERALL (z-score > 3)
z_scores = data_concat.iloc[:,2:755].transform(lambda x : zscore(x,ddof=1))
abs_z_scores = np.abs(z_scores)
filtered_entries = (abs_z_scores < 3).all(axis=1)
data_concat.iloc[:,2:755] = data_concat.iloc[:,2:755][filtered_entries]

In [ ]:
#Transform the data to log10 (OPTIONAL)

#data_log = data_concat
#data_log.iloc[:,2:755] = np.log10(data_log.iloc[:,2:755])

In [12]:
# Taking the mean for each kinase

concat_mean = data_concat.groupby(['GENE']).mean().reset_index()
concat_mean = concat_mean.drop(['Batch'], axis=1)

In [13]:
#NORMALIZATION USING STANDARD SCALER
scaler = StandardScaler()

concat_mean.iloc[:,2:755] = scaler.fit_transform(concat_mean.iloc[:,2:755].to_numpy())

In [14]:
#MAKE GENE AS INDEX
concat_mean.set_index('GENE', inplace=True)

In [ ]:
#Clustermap

ax = sns.clustermap(concat_mean,
                    z_score = 0,
                    cmap="vlag",
                    center=0, 
                    vmin = -1,
                    vmax = 1,
                    yticklabels=True,
                    xticklabels=True,
                    figsize=(125, 125),
                    linewidth=.5)

plt.title('Cluster map of Kinase-Lipid before batch correction -Non-normalized-', fontsize = 60) # title with fontsize 20
plt.xlabel('Lipids', fontsize = 80) # x-axis label with fontsize 15
plt.ylabel('Kinases', fontsize =80) # y-axis label with fontsize 15

#ax.savefig("logdata_zscore_lim5.png")

In [10]:
# Batch Effect correction

mod = patsy.dmatrix("GENE", data_concat, return_type="dataframe")

ebat = combat(data_concat.iloc[:,2:755].T, data_concat['Batch'], mod)

found 20 batches
found 0 numerical covariates...
found 715 categorical variables:	GENE[T.AATK ], GENE[T.ABCC1 ], GENE[T.ABL1 ], GENE[T.ABL2 ], GENE[T.ACVR1 ], GENE[T.ACVR1B ], GENE[T.ACVR1C ], GENE[T.ACVR2A ], GENE[T.ACVR2B ], GENE[T.ACVRL1 ], GENE[T.ADCK1 ], GENE[T.ADCK2 ], GENE[T.ADCK4 ], GENE[T.ADCK5 ], GENE[T.ADK ], GENE[T.ADRBK1 ], GENE[T.ADRBK2 ], GENE[T.AK1 ], GENE[T.AK2 ], GENE[T.AK3 ], GENE[T.AK3L1 ], GENE[T.AK3L2 ], GENE[T.AK5 ], GENE[T.AK7 ], GENE[T.AKAP13 ], GENE[T.AKT1 ], GENE[T.AKT2 ], GENE[T.AKT3 ], GENE[T.ALDH18A1 ], GENE[T.ALK ], GENE[T.ALPK1 ], GENE[T.ALPK2 ], GENE[T.ALPK3 ], GENE[T.ALS2CR2 ], GENE[T.ALS2CR7 ], GENE[T.AMHR2 ], GENE[T.ANKK1 ], GENE[T.ARAF ], GENE[T.ATM ], GENE[T.ATR ], GENE[T.AURKA ], GENE[T.AURKB ], GENE[T.AURKC ], GENE[T.AXL ], GENE[T.BAIAP2 ], GENE[T.BCKDK ], GENE[T.BCR ], GENE[T.BLK ], GENE[T.BMP2K ], GENE[T.BMPR1A ], GENE[T.BMPR1B ], GENE[T.BMPR2 ], GENE[T.BMX ], GENE[T.BRAF ], GENE[T.BRD2 ], GENE[T.BRD3 ], GENE[T.BRD4 ], GENE[T.BRDT ], GENE[T.BRS

Fitting L/S model and finding priors
Finding parametric adjustments


Adjusting data


In [23]:
batch = ebat.T
batch.insert(0, 'GENE', data_concat.iloc[:,[0]])
batch.insert(1, 'Batch', data_concat.iloc[:,[1]])

In [25]:
#Loading / Saving dataset after batch correction

#batch.to_csv('batch.csv')
batch = pd.read_csv('batch.csv')

In [21]:
#NORMALIZATION USING STANDARD SCALER
scaler = StandardScaler()

batch.iloc[:,2:755] = scaler.fit_transform(batch.iloc[:,2:755].to_numpy())

In [26]:
pd.set_option('display.max_rows', 10000)
batch['CL68:3_C16:0'].sort_values()

2574    -6.784036
2578    -6.783977
2579    -6.745989
2577    -6.731230
2575    -6.731048
2576    -6.721894
356     -5.643093
359     -5.554794
357     -5.459267
358     -5.422404
355     -5.256209
2925    -3.907065
2927    -3.850029
2923    -3.819459
2924    -3.803355
2926    -3.792775
2922    -3.753027
8577    -3.050925
2198    -3.050442
2200    -2.998806
354     -2.975893
2201    -2.948597
1095    -2.895303
1094    -2.895109
1097    -2.891068
8578    -2.880261
8506    -2.875915
8503    -2.873785
1093    -2.863103
1092    -2.860317
8504    -2.850823
1096    -2.841741
8502    -2.833853
8505    -2.828645
8576    -2.818601
8507    -2.743799
3271    -2.718005
8579    -2.614351
6933    -2.581158
6930    -2.559605
9027    -2.543757
6789    -2.536991
9028    -2.531170
5125    -2.524245
9024    -2.517866
6934    -2.516853
6931    -2.515412
7643    -2.510637
7641    -2.509424
7638    -2.503773
5128    -2.497888
8575    -2.496015
7642    -2.495958
6787    -2.491046
7640    -2.485968
5126    -2

In [15]:
batch_mean = batch.groupby(['GENE']).mean().reset_index()
batch_mean = batch_mean.drop(['Batch'], axis=1)

In [16]:
#MAKE GENE AS INDEX
batch_mean.set_index('GENE', inplace=True)

In [56]:
#Clustermap

ax = sns.clustermap(batch_mean,
                    z_score = 0,
                    cmap="vlag",
                    center=0, 
                    vmin = -1,
                    vmax = 1,
                    yticklabels=True,
                    xticklabels=True,
                    figsize=(125, 125),
                    linewidth=.5)

plt.title('Cluster map of Kinase-Lipid before batch correction -Non-normalized-', fontsize = 60) # title with fontsize 20
plt.xlabel('Lipids', fontsize = 80) # x-axis label with fontsize 15
plt.ylabel('Kinases', fontsize =80) # y-axis label with fontsize 15

ax.savefig("batch_mean")



In [59]:
#Filtering all the same lipids in one column / grouped by the name of lipids

filter_col_SM = [col for col in batch if col.startswith('SM')]
filter_col_GlcCer = [col for col in batch if col.startswith('Glc')]
filter_col_Cer = [col for col in batch if col.startswith('DHCer')] + [col for col in batch if col.startswith('Cer')]
filter_col_CL = [col for col in batch if col.startswith('CL')]
filter_col_LysoPC = [col for col in batch if col.startswith('LysoPC')]
filter_col_PC = [col for col in batch if col.startswith('PC')]
filter_col_LysoPE = [col for col in batch if col.startswith('LysoPE')]
filter_col_PE = [col for col in batch if col.startswith('PE')]
filter_col_LysoPI = [col for col in batch if col.startswith('LysoPI')]
filter_col_PI = [col for col in batch if col.startswith('PI')]
filter_col_LysoPS = [col for col in batch if col.startswith('LysoPS')]
filter_col_PS = [col for col in batch if col.startswith('PS')]

lipids_sum = filter_col_CL + filter_col_LysoPC + filter_col_PC + filter_col_LysoPE + filter_col_PE + filter_col_SM + filter_col_GlcCer + filter_col_Cer + filter_col_LysoPI + filter_col_PI + filter_col_LysoPS + filter_col_PS

In [60]:
#Sum up all the all the lipids with the same head-group

batch['CL_Sum'] = batch[filter_col_CL].sum(axis=1)
batch['LysoPC_Sum'] = batch[filter_col_LysoPC].sum(axis=1)
batch['PC_Sum'] = batch[filter_col_PC].sum(axis=1)
batch['LysoPE_Sum'] = batch[filter_col_LysoPE].sum(axis=1)
batch['PE_Sum'] = batch[filter_col_PE].sum(axis=1)
batch['SM_Sum'] = batch[filter_col_SM].sum(axis=1)
batch['GlcCer_Sum'] = batch[filter_col_GlcCer].sum(axis=1)
batch['Cer_Sum'] = batch[filter_col_Cer].sum(axis=1)
batch['LysoPI_Sum'] = batch[filter_col_LysoPI].sum(axis=1)
batch['PI_Sum'] = batch[filter_col_PI].sum(axis=1)
batch['LysoPS_Sum'] = batch[filter_col_LysoPS].sum(axis=1)
batch['PS_Sum'] = batch[filter_col_PS].sum(axis=1)

In [61]:
# Eliminate non-essential columns and keep only the sumed-up ones

features_sum = ['GENE', 'Batch', 'CL_Sum', 'LysoPC_Sum', 'PC_Sum',
                'LysoPE_Sum', 'PE_Sum', 'SM_Sum', 'GlcCer_Sum', 'Cer_Sum',
                'LysoPI_Sum', 'PI_Sum', 'LysoPS_Sum', 'PS_Sum']
batch_sum = batch[features_sum]

In [67]:
pd.set_option('display.max_rows', 800)
batch_sum_mean

GENE     CL_Sum  LysoPC_Sum     PC_Sum  LysoPE_Sum     PE_Sum  \
0            AAK1   -0.060707    0.014474  -0.105554    0.124414   0.153166   
1            AATK    0.012171    0.003587   0.025991    0.011670  -0.012830   
2           ABCC1   -0.021623   -0.097174  -0.123020   -0.022482  -0.001137   
3            ABL1   -0.054295    0.054963   0.018844    0.058461   0.028600   
4            ABL2   -0.024784    0.264585   0.202978    0.094102   0.088362   
5           ACVR1    0.079399    0.007097   0.030606    0.001038   0.012219   
6          ACVR1B    0.008001    0.001086   0.017722    0.007935  -0.015410   
7          ACVR1C   -0.116088   -0.017266  -0.028627   -0.045636  -0.060568   
8          ACVR2A    0.082540   -0.017414   0.030319   -0.019593   0.007653   
9          ACVR2B   -0.037620   -0.131189  -0.074973   -0.022809  -0.016873   
10         ACVRL1   -0.090768   -0.049605  -0.000684    0.028729   0.014997   
11          ADCK1   -0.216512   -0.075680  -0.103680   -0.083488  -0.052607   
12          ADCK2   -0.036572   -0.032429   0.102931    0.090408   0.053270   
13          ADCK4   -0.203455   -0.059325  -0.040576   -0.090467  -0.027643   
14          ADCK5   -0.026845   -0.037922  -0.067292    0.016007  -0.007621   
15            ADK   -0.111375   -0.184894  -0.066712   -0.414481  -0.303861   
16         ADRBK1   -0.072790   -0.035693  -0.038636    0.003209  -0.000441   
17         ADRBK2    0.070463    0.027326   0.027073    0.019592   0.002611   
18            AK1    0.102967   -0.015259   0.053948   -0.034241   0.025683   
19            AK2   -0.062612    0.010394  -0.100074    0.122778   0.178881   
20            AK3    0.355239   -0.087676  -0.065165   -0.105263  -0.116758   
21          AK3L1   -0.035335    0.080769   0.042344    0.061121   0.044802   
22          AK3L2   -0.186116   -0.206356  -0.107399   -0.166867  -0.026647   
23            AK5   -0.076156   -0.011224  -0.019502   -0.059057  -0.048723   
24            AK7   -0.072696   -0.021449  -0.024736   -0.059596  -0.048355   
25         AKAP13   -0.095317   -0.186967  -0.040765   -0.007967   0.134982   
26           AKT1    0.034424    0.062766   0.058312    0.052433   0.015801   
27           AKT2    0.091666   -0.005296   0.032314   -0.001904   0.002866   
28           AKT3   -0.099322   -0.095816  -0.055444   -0.137755  -0.118608   
29       ALDH18A1    1.480800   -1.201888  -0.134483   -0.757335  -1.194248   
30            ALK    0.008707    0.001004   0.027283    0.006942  -0.015041   
31          ALPK1   -0.203136   -0.093619  -0.029068   -0.105074  -0.043385   
32          ALPK2    0.034983   -0.027358  -0.017346   -0.025154  -0.015657   
33          ALPK3   -0.176177   -0.030822  -0.068613    0.002021  -0.054301   
34        ALS2CR2   -0.194381   -0.069781  -0.088130   -0.094381  -0.046237   
35        ALS2CR7   -0.061931   -0.059209  -0.058558   -0.044780  -0.031382   
36          AMHR2   -0.200054   -0.072255  -0.073550   -0.081931  -0.034197   
37          ANKK1   -0.213038   -0.931328  -0.206274   -0.478430  -0.235322   
38           ARAF    0.077682   -0.038339   0.014950   -0.017060  -0.009386   
39            ATM   -0.074697    0.023564   0.020456    0.150069   0.171829   
40            ATR   -0.025408   -0.076466  -0.075408   -0.017013  -0.018011   
41          AURKA    0.086111   -0.202890   0.006426   -0.197558  -0.048463   
42          AURKB    0.015068    0.014443   0.038405    0.014124  -0.008815   
43          AURKC   -0.021437   -0.139096  -0.134153   -0.022560  -0.034254   
44            AXL    0.150959    0.056559   0.085322    0.051746   0.055353   
45         BAIAP2   -0.095885   -0.032372  -0.029284   -0.119902  -0.058238   
46          BCKDK   -0.174782   -0.073423  -0.040352   -0.060756  -0.052250   
47            BCR    0.011469    0.002539   0.019083    0.006143  -0.014843   
48            BLK   -0.175424   -0.035184   0.006468   -0.010039  -0.034793   
49          BMP2K   -0.184665    0.022306  -0.020843   -0.008220

In [64]:
#NORMALIZATION OF THE SUM DATA USING STANDARD SCALER
scaler = StandardScaler()

batch_sum.iloc[:,2:14] = scaler.fit_transform(batch_sum.iloc[:,2:14].to_numpy())

/Users/pablo/opt/anaconda3/envs/lipidomics/lib/python3.8/site-packages/pandas/core/indexing.py:966: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[item] = s


In [66]:
#Grouping by Gene and take mean / elimination of unnecesary columns

batch_sum_mean = batch_sum.groupby(['GENE']).mean().reset_index()
batch_sum_mean = batch_sum_mean.drop(['Batch'], axis=1)

In [68]:
#MAKE GENE AS INDEX
batch_sum_mean.set_index('GENE', inplace=True) 

In [72]:
#Clustermap

ax = sns.clustermap(batch_sum_mean, 
                    cmap="vlag",
                    center=0,
                    vmin = -0.5,
                    vmax = 0.5,
                    yticklabels=True,
                    square=True,
                    xticklabels=True,
                    figsize=(125, 125),
                    linewidth=.5)

plt.title('Cluster map of Kinase-Lipid Batch corrected data sumed up according headgroup', fontsize = 60) # title with fontsize 20
plt.xlabel('Lipids', fontsize = 80) # x-axis label with fontsize 15
plt.ylabel('Kinases', fontsize =80) # y-axis label with fontsize 15

ax.savefig("batch_sum_headgroup.png")




In [ ]:
#Generating the transposed matrix with lipids in the rows and kinases in the columns

lipids_batch = batch_dataset.T
lipids_batch = lipids_batch.reset_index()

In [ ]:
lipids_batch.columns = lipids_batch.iloc[0]
lipids_batch = lipids_batch.drop(lipids_batch.index[0])

In [ ]:
lipids_batch.to_csv('lipids_batch.txt', header=True, index=False, sep='\t')
batch_dataset.to_csv('batch_dataset.txt', header=True, index=False, sep='\t')

In [ ]:
batch_dataset = pd.read_csv('batch_dataset.txt', sep='\t')
lipids_batch = pd.read_csv('lipids_batch.txt', sep='\t')

In [ ]:
#Calculate z-score
from scipy.stats import zscore
zlog_batch = log_batch.apply(zscore)

In [ ]:
pd.set_option('display.max_rows', 800)
#pd.set_option('display.max_columns', 800)
log_batch.isnull().sum()